In [1]:
fname = "/Users/gc3045/laml2_experiments/BaseMEM_Magic/gillian/baseMemoir_result_df_remapped.csv"

In [78]:
import csv
from Bio import SeqIO
from Bio import AlignIO
import pandas as pd
import os
import json
import numpy as np

In [22]:
nexus_taxlabels = {
    "p2_barcs.nexus": [1, 3, 4, 5, 6, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 20, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35],
    
    "p3_barcs.nexus": [1, 2, 3, 4, 5, 6, 7, 9, 10, 11, 12, 13, 14, 15, 16],
    
    "p4_barcs.nexus": [1, 5, 6, 7, 9, 10, 11, 12, 13, 14, 15, 16, 17, 19, 21, 22, 23, 24],
    
    "p5_barcs.nexus": [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 20, 21, 22, 23, 24, 25, 26, 27, 28],
    
    "p6_barcs.nexus": [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 16, 17],
    
    "p78_barcs.nexus": [3, 4, 5, 6, 8, 9, 10, 11, 18, 20, 21, 24, 25, 31, 34, 37, 39, 40, 41, 43, 46, 48, 49, 50, 51, 53, 54, 55, 56, 58, 62, 64, 65, 68, 69, 72, 73, 74, 75, 77, 78, 81, 82, 83, 84, 85, 86, 87, 89, 90],
    
    "p910_barcs.nexus": [1, 9, 12, 14, 15, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 28, 29, 30, 31, 32, 33, 34, 35, 37, 38, 39, 40, 42, 43, 44, 45, 46, 47, 48, 49, 50, 52, 53, 55, 56, 57]
}

I could process the .nexus files into json or charMats, or
I could process the result_df I have into json and then try to match
across the two.

The fear is that there are more taxa labels in the nexus files than 
unique cell identifiers in my result_df. Also, I know they did some 
merging of probabilities according to the FISHseq data. 

```
Some positions (0/1, 7/8, 9/10) are offest images of the same colony. I will merge cells imaged twice by averaging probabilities
```

Maybe it's cell index by unique location. 

In [368]:
df = pd.read_csv(fname)

df.groupby('position')

integration_barcode  cell_number  dot_number  position_number   
0                      1.0          1.0        57.0              1.0  \
1                      1.0          1.0        57.0              1.0   
2                      1.0          1.0        57.0              1.0   
3                      1.0          1.0        57.0              1.0   
4                      1.0          1.0        57.0              1.0   
...                    ...          ...         ...              ...   
90463                  9.0          9.0       649.0              9.0   
90464                  9.0          9.0       649.0              9.0   
90465                  9.0          9.0       649.0              9.0   
90466                  9.0          9.0       649.0              9.0   
90467                  9.0          9.0       649.0              9.0   

       site_index  feature_1  feature_2  feature_3  feature_4  feature_5  ...   
0             1.0  10.984123   8.966101  10.065734   7.761319   6.930495  ...  \
1             2.0  10.861515   8.056427   8.837100  11.704025   6.620073  ...   
2             3.0   7.203406  10.781100   7.641564   8.145260   2.833213  ...   
3             4.0   6.924612  10.706117   7.285507   7.573017   2.484907  ...   
4             5.0  10.343901   8.582606  10.566330  10.339126   6.424869  ...   
...           ...        ...        ...        ...        ...        ...  ...   
90463         2.0   6.735780  10.173782   7.367709   8.249836   3.091042  ...   
90464         3.0   6.753438  10.685995   7.773174   7.355002   2.639057  ...   
90465         4.0   5.176150  10.653606   8.835792   5.726848   0.000000  ...   
90466         5.0  10.038106   8.198089   5.505332  10.433056   6.224558  ...   
90467         6.0   8.503297  10.389118   7.581210   8.083020   4.727388  ...   

       intensity_channel2  intensity_channel3  intensity_channel4   
0                    65.0                35.0                65.0  \
1                    65.0                65.0                50.0   
2                    41.0                 5.0                65.0   
3                    41.0                 4.0                65.0   
4                    65.0                42.0                39.0   
...                   ...                 ...                 ...   
90463                27.0                35.0                35.0   
90464                35.0                35.0                35.0   
90465                35.0                35.0                35.0   
90466                35.0                35.0                35.0   
90467                35.0                35.0                35.0   

       maxpostprobstate_at_site  maxpostprobval_at_site       state_0   
0                           1.0                0.909489  5.995518e-18  \
1                           3.0                0.644814  1.999991e-17   
2                           0.0                0.940735  1.881959e-11   
3                           0.0                0.942045  1.603485e-14   
4                           1.0                0.567286  1.890085e-35   
...                         ...                     ...           ...   
90463                       0.0                0.979866  1.193092e-09   
90464                       0.0                0.987961  1.290770e-07   
90465                       0.0                0.966041  3.868813e-09   
90466                       1.0                0.664211  1.636422e-23   
90467                       0.0                0.913224  9.545623e-14   

            state_1        state_2       state_3  KDE_max_state  
0      1.132963e-10   6.091644e-19  1.705798e-69              1  
1      1.399712e-13   1.332736e-19  4.175912e-14              1  
2      6.889248e-19   4.426716e-16  6.129712e-13              0  
3      7.138131e-29   5.265846e-16  1.032066e-32              0  
4      2.280929e-14   1.780643e-15  9.252995e-19              1  
...             ...            ...           ...            ...  
9

In [184]:
position_groups = df.groupby('position_number')
for position, position_data in position_groups:
    cell_groups = position_data.groupby('cell_number')
    for cell, cell_data in cell_groups:
        integration_groups = cell_data.groupby('integration_barcode')
        for integration_group, integration_group_data in integration_groups:
            site_groups = integration_group_data.groupby('site_index')
            print(position, cell, integration_group, len(site_groups))

0.0 3.0 1.0 6
0.0 3.0 2.0 6
0.0 3.0 6.0 6
0.0 3.0 7.0 6
0.0 3.0 9.0 6
0.0 3.0 13.0 6
0.0 3.0 15.0 6
0.0 3.0 16.0 6
0.0 3.0 17.0 6
0.0 3.0 21.0 6
0.0 3.0 24.0 6
0.0 3.0 25.0 6
0.0 3.0 29.0 6
0.0 3.0 30.0 6
0.0 3.0 33.0 6
0.0 3.0 37.0 6
0.0 3.0 40.0 6
0.0 3.0 42.0 6
0.0 3.0 44.0 6
0.0 3.0 46.0 6
0.0 3.0 48.0 6
0.0 3.0 49.0 6
0.0 3.0 50.0 6
0.0 3.0 54.0 6
0.0 3.0 58.0 6
0.0 3.0 61.0 6
0.0 4.0 1.0 6
0.0 4.0 15.0 6
0.0 4.0 16.0 6
0.0 4.0 18.0 6
0.0 4.0 23.0 6
0.0 4.0 24.0 6
0.0 4.0 28.0 6
0.0 4.0 30.0 6
0.0 4.0 35.0 6
0.0 4.0 40.0 6
0.0 4.0 42.0 6
0.0 4.0 46.0 6
0.0 4.0 49.0 6
0.0 4.0 59.0 6
0.0 5.0 1.0 6
0.0 5.0 4.0 6
0.0 5.0 5.0 6
0.0 5.0 6.0 6
0.0 5.0 9.0 6
0.0 5.0 10.0 6
0.0 5.0 14.0 6
0.0 5.0 15.0 6
0.0 5.0 18.0 6
0.0 5.0 19.0 6
0.0 5.0 21.0 6
0.0 5.0 25.0 6
0.0 5.0 29.0 6
0.0 5.0 30.0 6
0.0 5.0 34.0 6
0.0 5.0 35.0 6
0.0 5.0 39.0 6
0.0 5.0 42.0 6
0.0 5.0 45.0 6
0.0 5.0 48.0 6
0.0 5.0 49.0 6
0.0 5.0 51.0 6
0.0 5.0 54.0 6
0.0 5.0 55.0 6
0.0 5.0 57.0 6
0.0 5.0 58.0 6
0.0 5.0 59.0 6
0.0 5.

2.0 24.0 46.0 6
2.0 24.0 47.0 6
2.0 24.0 48.0 6
2.0 24.0 50.0 6
2.0 24.0 51.0 6
2.0 24.0 52.0 6
2.0 24.0 55.0 6
2.0 24.0 57.0 6
2.0 24.0 58.0 6
2.0 24.0 60.0 6
2.0 24.0 61.0 6
2.0 24.0 62.0 6
2.0 24.0 63.0 6
2.0 24.0 64.0 6
2.0 24.0 65.0 6
2.0 25.0 1.0 6
2.0 25.0 2.0 6
2.0 25.0 3.0 6
2.0 25.0 4.0 6
2.0 25.0 5.0 6
2.0 25.0 6.0 6
2.0 25.0 8.0 6
2.0 25.0 9.0 6
2.0 25.0 10.0 6
2.0 25.0 11.0 6
2.0 25.0 13.0 6
2.0 25.0 14.0 6
2.0 25.0 15.0 6
2.0 25.0 18.0 6
2.0 25.0 19.0 6
2.0 25.0 20.0 6
2.0 25.0 21.0 6
2.0 25.0 22.0 6
2.0 25.0 23.0 6
2.0 25.0 26.0 6
2.0 25.0 27.0 6
2.0 25.0 29.0 6
2.0 25.0 30.0 6
2.0 25.0 31.0 6
2.0 25.0 32.0 6
2.0 25.0 33.0 6
2.0 25.0 34.0 6
2.0 25.0 35.0 6
2.0 25.0 36.0 6
2.0 25.0 37.0 6
2.0 25.0 38.0 6
2.0 25.0 40.0 6
2.0 25.0 41.0 6
2.0 25.0 42.0 6
2.0 25.0 43.0 6
2.0 25.0 44.0 6
2.0 25.0 46.0 6
2.0 25.0 47.0 6
2.0 25.0 48.0 6
2.0 25.0 50.0 6
2.0 25.0 51.0 6
2.0 25.0 53.0 6
2.0 25.0 54.0 6
2.0 25.0 55.0 6
2.0 25.0 56.0 6
2.0 25.0 59.0 6
2.0 25.0 60.0 6
2.0 25.0 61.0 6


4.0 19.0 3.0 6
4.0 19.0 5.0 6
4.0 19.0 6.0 6
4.0 19.0 9.0 6
4.0 19.0 10.0 6
4.0 19.0 11.0 6
4.0 19.0 12.0 6
4.0 19.0 16.0 6
4.0 19.0 19.0 6
4.0 19.0 21.0 6
4.0 19.0 22.0 6
4.0 19.0 23.0 6
4.0 19.0 24.0 6
4.0 19.0 25.0 6
4.0 19.0 26.0 6
4.0 19.0 27.0 6
4.0 19.0 28.0 6
4.0 19.0 29.0 6
4.0 19.0 30.0 6
4.0 19.0 31.0 6
4.0 19.0 32.0 6
4.0 19.0 33.0 6
4.0 19.0 34.0 6
4.0 19.0 36.0 6
4.0 19.0 37.0 6
4.0 19.0 38.0 6
4.0 19.0 40.0 6
4.0 19.0 41.0 6
4.0 19.0 42.0 6
4.0 19.0 43.0 6
4.0 19.0 45.0 6
4.0 19.0 46.0 6
4.0 19.0 47.0 6
4.0 19.0 48.0 6
4.0 19.0 52.0 6
4.0 19.0 53.0 6
4.0 19.0 54.0 6
4.0 19.0 55.0 6
4.0 19.0 56.0 6
4.0 19.0 59.0 6
4.0 19.0 61.0 6
4.0 19.0 65.0 6
4.0 20.0 2.0 6
4.0 20.0 3.0 6
4.0 20.0 5.0 6
4.0 20.0 6.0 6
4.0 20.0 8.0 6
4.0 20.0 10.0 6
4.0 20.0 11.0 6
4.0 20.0 12.0 6
4.0 20.0 13.0 6
4.0 20.0 14.0 6
4.0 20.0 15.0 6
4.0 20.0 16.0 6
4.0 20.0 17.0 6
4.0 20.0 18.0 6
4.0 20.0 19.0 6
4.0 20.0 20.0 6
4.0 20.0 21.0 6
4.0 20.0 22.0 6
4.0 20.0 23.0 6
4.0 20.0 24.0 6
4.0 20.0 26.0 6
4

6.0 10.0 31.0 6
6.0 10.0 32.0 6
6.0 10.0 33.0 6
6.0 10.0 34.0 6
6.0 10.0 36.0 6
6.0 10.0 38.0 6
6.0 10.0 39.0 6
6.0 10.0 40.0 6
6.0 10.0 41.0 6
6.0 10.0 42.0 6
6.0 10.0 43.0 6
6.0 10.0 44.0 6
6.0 10.0 46.0 6
6.0 10.0 47.0 6
6.0 10.0 48.0 6
6.0 10.0 49.0 6
6.0 10.0 51.0 6
6.0 10.0 54.0 6
6.0 10.0 55.0 6
6.0 10.0 56.0 6
6.0 10.0 58.0 6
6.0 10.0 59.0 6
6.0 10.0 60.0 6
6.0 10.0 61.0 6
6.0 10.0 62.0 6
6.0 10.0 63.0 6
6.0 10.0 64.0 6
6.0 10.0 65.0 6
6.0 10.0 66.0 6
6.0 11.0 1.0 6
6.0 11.0 3.0 6
6.0 11.0 5.0 6
6.0 11.0 8.0 6
6.0 11.0 9.0 6
6.0 11.0 12.0 6
6.0 11.0 13.0 6
6.0 11.0 14.0 6
6.0 11.0 15.0 6
6.0 11.0 16.0 6
6.0 11.0 17.0 6
6.0 11.0 19.0 6
6.0 11.0 20.0 6
6.0 11.0 21.0 6
6.0 11.0 22.0 6
6.0 11.0 23.0 6
6.0 11.0 26.0 6
6.0 11.0 27.0 6
6.0 11.0 28.0 6
6.0 11.0 29.0 6
6.0 11.0 30.0 6
6.0 11.0 32.0 6
6.0 11.0 34.0 6
6.0 11.0 36.0 6
6.0 11.0 40.0 6
6.0 11.0 42.0 6
6.0 11.0 43.0 6
6.0 11.0 44.0 6
6.0 11.0 45.0 6
6.0 11.0 47.0 6
6.0 11.0 48.0 6
6.0 11.0 50.0 6
6.0 11.0 51.0 6
6.0 11.0 52.0

7.0 49.0 40.0 6
7.0 49.0 41.0 6
7.0 49.0 42.0 6
7.0 49.0 44.0 6
7.0 49.0 46.0 6
7.0 49.0 47.0 6
7.0 49.0 48.0 6
7.0 49.0 50.0 6
7.0 49.0 51.0 6
7.0 49.0 52.0 6
7.0 49.0 54.0 6
7.0 49.0 56.0 6
7.0 49.0 57.0 6
7.0 49.0 59.0 6
7.0 49.0 66.0 6
7.0 50.0 1.0 6
7.0 50.0 5.0 6
7.0 50.0 9.0 6
7.0 50.0 12.0 6
7.0 50.0 14.0 6
7.0 50.0 15.0 6
7.0 50.0 16.0 6
7.0 50.0 18.0 6
7.0 50.0 21.0 6
7.0 50.0 27.0 6
7.0 50.0 30.0 6
7.0 50.0 33.0 6
7.0 50.0 35.0 6
7.0 50.0 36.0 6
7.0 50.0 37.0 6
7.0 50.0 41.0 6
7.0 50.0 42.0 6
7.0 50.0 43.0 6
7.0 50.0 44.0 6
7.0 50.0 46.0 6
7.0 50.0 47.0 6
7.0 50.0 48.0 6
7.0 50.0 51.0 6
7.0 50.0 52.0 6
7.0 50.0 55.0 6
7.0 50.0 56.0 6
7.0 50.0 59.0 6
7.0 50.0 62.0 6
7.0 50.0 66.0 6
7.0 51.0 1.0 6
7.0 51.0 3.0 6
7.0 51.0 5.0 6
7.0 51.0 6.0 6
7.0 51.0 8.0 6
7.0 51.0 9.0 6
7.0 51.0 10.0 6
7.0 51.0 11.0 6
7.0 51.0 12.0 6
7.0 51.0 15.0 6
7.0 51.0 16.0 6
7.0 51.0 17.0 6
7.0 51.0 18.0 6
7.0 51.0 22.0 6
7.0 51.0 25.0 6
7.0 51.0 27.0 6
7.0 51.0 28.0 6
7.0 51.0 33.0 6
7.0 51.0 34.0 6
7

8.0 38.0 32.0 6
8.0 38.0 34.0 6
8.0 38.0 35.0 6
8.0 38.0 36.0 6
8.0 38.0 37.0 6
8.0 38.0 38.0 6
8.0 38.0 39.0 6
8.0 38.0 41.0 6
8.0 38.0 44.0 6
8.0 38.0 46.0 6
8.0 38.0 48.0 6
8.0 38.0 49.0 6
8.0 38.0 50.0 6
8.0 38.0 51.0 6
8.0 38.0 52.0 6
8.0 38.0 53.0 6
8.0 38.0 55.0 6
8.0 38.0 56.0 6
8.0 38.0 58.0 6
8.0 38.0 59.0 6
8.0 38.0 60.0 6
8.0 38.0 61.0 6
8.0 38.0 62.0 6
8.0 38.0 64.0 6
8.0 38.0 65.0 6
8.0 38.0 66.0 6
8.0 39.0 1.0 6
8.0 39.0 5.0 6
8.0 39.0 7.0 6
8.0 39.0 8.0 6
8.0 39.0 9.0 6
8.0 39.0 10.0 6
8.0 39.0 12.0 6
8.0 39.0 15.0 6
8.0 39.0 20.0 6
8.0 39.0 23.0 6
8.0 39.0 26.0 6
8.0 39.0 29.0 6
8.0 39.0 32.0 6
8.0 39.0 33.0 6
8.0 39.0 34.0 6
8.0 39.0 35.0 6
8.0 39.0 36.0 6
8.0 39.0 40.0 6
8.0 39.0 42.0 6
8.0 39.0 44.0 6
8.0 39.0 46.0 6
8.0 39.0 47.0 6
8.0 39.0 48.0 6
8.0 39.0 50.0 6
8.0 39.0 51.0 6
8.0 39.0 52.0 6
8.0 39.0 56.0 6
8.0 39.0 57.0 6
8.0 39.0 59.0 6
8.0 39.0 66.0 6
8.0 40.0 1.0 6
8.0 40.0 4.0 6
8.0 40.0 8.0 6
8.0 40.0 9.0 6
8.0 40.0 10.0 6
8.0 40.0 15.0 6
8.0 40.0 16.0 6
8

9.0 35.0 45.0 6
9.0 35.0 47.0 6
9.0 35.0 49.0 6
9.0 35.0 50.0 6
9.0 35.0 51.0 6
9.0 35.0 53.0 6
9.0 35.0 54.0 6
9.0 35.0 55.0 6
9.0 35.0 56.0 6
9.0 35.0 59.0 6
9.0 35.0 61.0 6
9.0 35.0 64.0 6
9.0 36.0 1.0 6
9.0 36.0 2.0 6
9.0 36.0 3.0 6
9.0 36.0 5.0 6
9.0 36.0 6.0 6
9.0 36.0 8.0 6
9.0 36.0 9.0 6
9.0 36.0 12.0 6
9.0 36.0 13.0 6
9.0 36.0 14.0 6
9.0 36.0 15.0 6
9.0 36.0 16.0 6
9.0 36.0 19.0 6
9.0 36.0 20.0 6
9.0 36.0 21.0 6
9.0 36.0 24.0 6
9.0 36.0 26.0 6
9.0 36.0 27.0 6
9.0 36.0 28.0 6
9.0 36.0 29.0 6
9.0 36.0 30.0 6
9.0 36.0 31.0 6
9.0 36.0 32.0 6
9.0 36.0 34.0 6
9.0 36.0 38.0 6
9.0 36.0 40.0 6
9.0 36.0 43.0 6
9.0 36.0 45.0 6
9.0 36.0 46.0 6
9.0 36.0 47.0 6
9.0 36.0 50.0 6
9.0 36.0 51.0 6
9.0 36.0 52.0 6
9.0 36.0 53.0 6
9.0 36.0 54.0 6
9.0 36.0 55.0 6
9.0 36.0 56.0 6
9.0 36.0 57.0 6
9.0 36.0 58.0 6
9.0 36.0 59.0 6
9.0 36.0 60.0 6
9.0 36.0 62.0 6
9.0 36.0 63.0 6
9.0 36.0 65.0 6
9.0 36.0 66.0 6
9.0 37.0 1.0 6
9.0 37.0 2.0 6
9.0 37.0 3.0 6
9.0 37.0 4.0 6
9.0 37.0 6.0 6
9.0 37.0 7.0 6
9.0 3

10.0 39.0 1.0 6
10.0 39.0 3.0 6
10.0 39.0 7.0 6
10.0 39.0 10.0 6
10.0 39.0 11.0 6
10.0 39.0 12.0 6
10.0 39.0 13.0 6
10.0 39.0 16.0 6
10.0 39.0 17.0 6
10.0 39.0 18.0 6
10.0 39.0 19.0 6
10.0 39.0 20.0 6
10.0 39.0 21.0 6
10.0 39.0 23.0 6
10.0 39.0 24.0 6
10.0 39.0 25.0 6
10.0 39.0 26.0 6
10.0 39.0 27.0 6
10.0 39.0 28.0 6
10.0 39.0 29.0 6
10.0 39.0 30.0 6
10.0 39.0 31.0 6
10.0 39.0 34.0 6
10.0 39.0 36.0 6
10.0 39.0 37.0 6
10.0 39.0 38.0 6
10.0 39.0 39.0 6
10.0 39.0 40.0 6
10.0 39.0 42.0 6
10.0 39.0 43.0 6
10.0 39.0 44.0 6
10.0 39.0 45.0 6
10.0 39.0 46.0 6
10.0 39.0 47.0 6
10.0 39.0 48.0 6
10.0 39.0 50.0 6
10.0 39.0 51.0 6
10.0 39.0 52.0 6
10.0 39.0 53.0 6
10.0 39.0 56.0 6
10.0 39.0 60.0 6
10.0 39.0 61.0 6
10.0 39.0 63.0 6
10.0 39.0 64.0 6
10.0 39.0 65.0 6
10.0 40.0 1.0 6
10.0 40.0 3.0 6
10.0 40.0 4.0 6
10.0 40.0 6.0 6
10.0 40.0 8.0 6
10.0 40.0 9.0 6
10.0 40.0 11.0 6
10.0 40.0 12.0 6
10.0 40.0 13.0 6
10.0 40.0 15.0 6
10.0 40.0 17.0 6
10.0 40.0 18.0 6
10.0 40.0 19.0 6
10.0 40.0 23.0 6
10.0 4

In [185]:
np.unique(df['integration_barcode'])

array([ 1.,  2.,  3.,  4.,  5.,  6.,  7.,  8.,  9., 10., 11., 12., 13.,
       14., 15., 16., 17., 18., 19., 20., 21., 22., 23., 24., 25., 26.,
       27., 28., 29., 30., 31., 32., 33., 34., 35., 36., 37., 38., 39.,
       40., 41., 42., 43., 44., 45., 46., 47., 48., 49., 50., 51., 52.,
       53., 54., 55., 56., 57., 58., 59., 60., 61., 62., 63., 64., 65.,
       66.])

### transform into json

In [186]:
# check if there are 66 integration barcodes 

result_json = {'cell_data': []}
position_groups = df.groupby('position_number')
for position, position_data in position_groups:
    cell_groups = position_data.groupby('cell_number')
    
    for cell, cell_data in cell_groups:
        cell_json = {'cell_name': cell, 'cassettes': []}

        integration_groups = cell_data.groupby('integration_barcode')
        print(len(integration_groups))

26
14
30
18
20
20
14
18
20
11
20
15
7
23
17
20
7
14
3
20
32
17
36
24
14
19
9
22
22
19
16
33
22
43
36
30
34
25
13
28
18
19
20
15
16
20
12
18
14
5
19
13
15
7
1
54
56
52
48
54
45
48
41
45
39
43
58
41
43
31
47
40
43
40
47
43
43
57
49
52
24
45
32
44
57
53
59
49
43
52
56
53
47
51
54
53
55
53
61
52
52
46
55
56
60
28
52
42
39
49
49
43
48
34
35
41
37
39
48
44
41
40
44
49
42
54
42
52
43
46
45
43
55
53
52
52
52
60
53
55
41
48
46
46
47
46
51
41
52
39
54
52
51
49
50
49
49
49
56
54
56
50
59
50
53
41
28
43
57
53
42
51
57
53
48
61
55
31
31
36
36
33
45
45
28
35
31
35
41
44
31
36
42
42
52
51
36
31
31
53
29
50
41
35
33
27
33
35
39
32
48
39
37
37
35
38
35
19
40
33
41
46
33
30
35
29
41
30
42
52
44
38
41
45
44
46
16
36
27
20
37
37
40
36
34
32
38
43
35
48
43
46
34
42
55
49
28
44
52
23
43
28
49
35
20
46
27
30
16
36
30
31
40
38
47
34
41
49
44
37
48
30
24
43
27
49
44
36
50
47
55
42
34
47
30
38
35
40
42
48
31
41
36
34
50
49
31
33
42
35
43
42
30
49
46
37
43
49
44
40
37
45
49
39
50
39
46
48
47
39
45
45
52
40
47
38

In [299]:
result_json = {'cell_data': []}
position_groups = df.groupby('position_number')
for position, position_data in position_groups:
    cell_groups = position_data.groupby('cell_number')
    
    for cell, cell_data in cell_groups:
        cell_json = {'cell_name': f'pos{int(position)}_cell{int(cell)}', 'cassettes': [], 
                     'position': int(position),
                     'cell_idx': int(cell)
                    }
        
        cassette_indices = set()
        integration_groups = cell_data.groupby('integration_barcode')
        for integration_barcode, integration_group_data in integration_groups:
            cassette_indices.add(integration_barcode)
            cassette_json = {
                "cassette_id": integration_barcode,
                "count_data": []
            }
            site_groups = integration_group_data.groupby('site_index')
            count_data_dict = {}
            allele = []
            for site, site_data in site_groups:
                # print(site, site_data)
                site = int(site) - 1
                count_data_dict[f'site_{site}'] = int(site_data['KDE_max_state'].values[0]) # maxKDEprob state
                allele.append(int(site_data['KDE_max_state'].values[0]))
                
                count_data_dict[f'emissions_site_{site}'] = dict()
                count_data_dict[f'emissions_site_{site}']['probGen_KDE_true_state_0'] = site_data['state_0'].values[0] # probGen_KDE_true_state_0 
                count_data_dict[f'emissions_site_{site}']['probGen_KDE_true_state_1'] = site_data['state_1'].values[0] # probGen_KDE_true_state_1
                count_data_dict[f'emissions_site_{site}']['probGen_KDE_true_state_2'] = site_data['state_2'].values[0] # probGen_KDE_true_state_1
                count_data_dict[f'emissions_site_{site}']['probGen_KDE_true_state_3'] = site_data['state_3'].values[0] # probGen_KDE_true_state_1

            count_data_dict['allele'] = allele
            cassette_json['count_data'].append(count_data_dict)
            
            cell_json['cassettes'].append(cassette_json)
        
        # fill in the missing integration_barcodes
        for i in range(1, 67): 
            if i not in cassette_indices:
                cassette_json = {
                    "cassette_id": i,
                    "count_data": []
                }
                cell_json['cassettes'].append(cassette_json)
        result_json['cell_data'].append(cell_json)


In [300]:
result_json['cell_data'][0]

{'cell_name': 'pos0_cell3',
 'cassettes': [{'cassette_id': 1.0,
   'count_data': [{'site_0': 0,
     'emissions_site_0': {'probGen_KDE_true_state_0': 2.898403920993961e-13,
      'probGen_KDE_true_state_1': 1.0283136935057907e-26,
      'probGen_KDE_true_state_2': 2.7608711258276563e-19,
      'probGen_KDE_true_state_3': 7.844834049135391e-20},
     'site_1': 0,
     'emissions_site_1': {'probGen_KDE_true_state_0': 4.5359074374609086e-10,
      'probGen_KDE_true_state_1': 9.103226395969624e-13,
      'probGen_KDE_true_state_2': 2.0520511142006627e-67,
      'probGen_KDE_true_state_3': 2.716203778963272e-19},
     'site_2': 0,
     'emissions_site_2': {'probGen_KDE_true_state_0': 1.0504111422719248e-11,
      'probGen_KDE_true_state_1': 2.712338826374149e-46,
      'probGen_KDE_true_state_2': 3.0207367790672962e-43,
      'probGen_KDE_true_state_3': 6.141698882323247e-69},
     'site_3': 0,
     'emissions_site_3': {'probGen_KDE_true_state_0': 2.236619460915008e-11,
      'probGen_KDE_t

In [189]:
json_string = json.dumps(result_json, indent=4)
with open("/Users/gc3045/laml2_experiments/proc_realdata/baseMemoir.json", "w") as f:
    f.write(json_string)

In [301]:
test_json = {'cell_data': result_json['cell_data'][0:5]}
# drop any cassettes which are all empty

cassettes_to_remove = {}
# First pass: Identify cassettes with length 0 in all cells
for cell_data in test_json['cell_data']:
    for cassette_data in cell_data['cassettes']:
#         print(cassette_data)
        cassette_id = cassette_data['cassette_id']
        if len(cassette_data['count_data']) == 0:
            cassettes_to_remove[cassette_id] = cassettes_to_remove.get(cassette_id, 0) + 1

# # Identify cassettes that are empty in all cells
cassettes_to_remove = {k for k, v in cassettes_to_remove.items() if v == len(test_json['cell_data'])}
# print(cassettes_to_remove)

# Second pass: Remove identified cassettes from all cells
for cell_data in test_json['cell_data']:
    cell_data['cassettes'] = [cassette for cassette in cell_data['cassettes'] if cassette['cassette_id'] not in cassettes_to_remove]

In [302]:

# drop to two cassettes
for cell_data in test_json['cell_data']:
    cell_data['cassettes'] = [cassette for cassette in cell_data['cassettes'] if cassette['cassette_id'] in {1.0, 2.0}] 
    # print(len([cassette for cassette in cell_data['cassettes'] if cassette['cassette_id'] in {1.0, 2.0}]))

# Print the updated test_json to verify
# test_json_str = json.dumps(test_json, indent=4)

json_string = json.dumps(test_json, indent=4)
#with open("/Users/gc3045/laml2_experiments/proc_realdata/baseMemoir_test.json", "w") as f:
with open("/Users/gc3045/scmail_v1/LAML/examples/example5/baseMemoir_test_small.json", "w") as f:

    f.write(json_string)

In [303]:
print([len(x['cassettes']) for x in test_json['cell_data']])


[2, 2, 2, 2, 2]


In [269]:
for cell_data in test_json['cell_data']:
    # print(len(cell_data['cassettes']))
    print(cell_data['cassettes'])

[{'cassette_id': 1.0, 'count_data': [{'site_0': 0, 'emissions_site_0': {'probGen_KDE_true_state_0': 2.898403920993961e-13, 'probGen_KDE_true_state_1': 1.0283136935057907e-26, 'probGen_KDE_true_state_2': 2.7608711258276563e-19, 'probGen_KDE_true_state_3': 7.844834049135391e-20}, 'site_1': 0, 'emissions_site_1': {'probGen_KDE_true_state_0': 4.5359074374609086e-10, 'probGen_KDE_true_state_1': 9.103226395969624e-13, 'probGen_KDE_true_state_2': 2.0520511142006627e-67, 'probGen_KDE_true_state_3': 2.716203778963272e-19}, 'site_2': 0, 'emissions_site_2': {'probGen_KDE_true_state_0': 1.0504111422719248e-11, 'probGen_KDE_true_state_1': 2.712338826374149e-46, 'probGen_KDE_true_state_2': 3.0207367790672962e-43, 'probGen_KDE_true_state_3': 6.141698882323247e-69}, 'site_3': 0, 'emissions_site_3': {'probGen_KDE_true_state_0': 2.236619460915008e-11, 'probGen_KDE_true_state_1': 7.5395596264151e-20, 'probGen_KDE_true_state_2': 3.106575404463873e-92, 'probGen_KDE_true_state_3': 3.3082301355541576e-47}, '

### assume independence between all target sites, forget cassettes 

In [369]:
# write to character matrix
char_mtrx = dict()
emission_mtrx = dict()

position_groups = df.groupby('position_number')
for position, position_data in position_groups:
    cell_groups = position_data.groupby('cell_number')
    
    for cell, cell_data in cell_groups:
        cell_name = f'pos{int(position)}_cell{int(cell)}'
        char_mtrx[cell_name] = dict()
        emission_mtrx[cell_name] = dict()
        
        integration_groups = cell_data.groupby('integration_barcode')
        cassette_indices = set()
        for integration_barcode, integration_group_data in integration_groups:
            
            site_groups = integration_group_data.groupby('site_index')
            allele = []
            emission_mtrx[cell_name][int(integration_barcode)] = []
            for site, site_data in site_groups:
                site = int(site) - 1
                allele.append(int(site_data['KDE_max_state'].values[0]))
                
                site_list = [site_data['state_0'].values[0], site_data['state_1'].values[0],
                            site_data['state_2'].values[0], site_data['state_3'].values[0]]
                
                emission_mtrx[cell_name][int(integration_barcode)].append(site_list)
          
            char_mtrx[cell_name][int(integration_barcode)] = allele
            cassette_indices.add(int(integration_barcode))
            
        # fill in the missing integration_barcodes
        for i in range(1, 67): 
            if i not in cassette_indices:
                char_mtrx[cell_name][i] = [-1, -1, -1, -1, -1, -1]
                
# write emission matrix

In [370]:
char_mtrx

{'pos0_cell3': {1: [0, 0, 0, 0, 3, 0],
  2: [2, 0, 0, 0, 0, 0],
  6: [1, 0, 0, 0, 0, 2],
  7: [1, 0, 1, 2, 1, 1],
  9: [1, 0, 0, 3, 0, 0],
  13: [1, 0, 0, 0, 1, 0],
  15: [1, 2, 2, 3, 1, 0],
  16: [2, 1, 2, 3, 1, 1],
  17: [0, 3, 0, 2, 3, 0],
  21: [1, 0, 0, 2, 0, 0],
  24: [0, 1, 0, 0, 0, 3],
  25: [0, 0, 0, 0, 2, 0],
  29: [0, 2, 0, 0, 0, 1],
  30: [1, 2, 1, 3, 3, 1],
  33: [3, 0, 0, 0, 0, 0],
  37: [0, 0, 0, 3, 0, 2],
  40: [2, 2, 0, 0, 2, 0],
  42: [2, 0, 0, 0, 0, 0],
  44: [1, 2, 0, 3, 3, 0],
  46: [0, 3, 0, 1, 1, 0],
  48: [1, 0, 0, 0, 1, 0],
  49: [2, 0, 0, 0, 1, 0],
  50: [0, 3, 3, 3, 0, 0],
  54: [2, 0, 0, 3, 1, 0],
  58: [0, 0, 0, 0, 0, 0],
  61: [0, 3, 0, 2, 1, 1],
  3: [-1, -1, -1, -1, -1, -1],
  4: [-1, -1, -1, -1, -1, -1],
  5: [-1, -1, -1, -1, -1, -1],
  8: [-1, -1, -1, -1, -1, -1],
  10: [-1, -1, -1, -1, -1, -1],
  11: [-1, -1, -1, -1, -1, -1],
  12: [-1, -1, -1, -1, -1, -1],
  14: [-1, -1, -1, -1, -1, -1],
  18: [-1, -1, -1, -1, -1, -1],
  19: [-1, -1, -1, -1, -1, -1],

In [389]:
emission_mtrx['pos0_cell3']

{1: [[2.898403920993961e-13,
   1.0283136935057907e-26,
   2.7608711258276563e-19,
   7.844834049135391e-20],
  [4.5359074374609086e-10,
   9.103226395969624e-13,
   2.0520511142006627e-67,
   2.716203778963272e-19],
  [1.0504111422719248e-11,
   2.712338826374149e-46,
   3.0207367790672962e-43,
   6.141698882323247e-69],
  [2.236619460915008e-11,
   7.5395596264151e-20,
   3.106575404463873e-92,
   3.3082301355541576e-47],
  [1.5675867025451018e-14,
   2.0027965243772648e-35,
   3.7463687713692244e-148,
   9.784831275494805e-14],
  [3.6956756903253385e-17,
   2.0031769654578662e-53,
   5.85344185576517e-32,
   1.4005484543401652e-35]],
 2: [[5.7899037744413684e-24,
   3.174579397956286e-17,
   1.9287299200806981e-13,
   1.1614055566731256e-103],
  [2.405994788194221e-11,
   3.12754444747096e-17,
   9.108143313514374e-15,
   3.633714996450186e-19],
  [5.878796116476981e-10,
   2.050256869776696e-64,
   1.347883646151249e-10,
   2.430060633482435e-21],
  [1.2644542321815142e-07,
   3.52

In [ ]:
header = ['cell_names']
for i in range(0, 66):
    for j in range(6):
        site_header = f'c{i}_s{j}'
        header.append(site_header)

flatten_char_mtrx = [header]
        
for cell_name in char_mtrx:
    # print(cell_name)
    cell_data = [cell_name]
    for i in range(1, 67): # still accessing them with names ranging from 1-67
        cell_data.extend(char_mtrx[cell_name][i])
    flatten_char_mtrx.append(cell_data)

In [390]:
emission_mtrx

flatten_emission_mtrx = [header]
for cell_name in emission_mtrx:
    emission_data = [cell_name]

    for i in range(1,67):
        if i in emission_mtrx[cell_name].keys():
            for site_emissions in emission_mtrx[cell_name][i]:
                emission_data.append(str(site_emissions))
        else:
            for i in range(6):
                emission_data.append([])
    # emission_mtrx_str = str(emission_mtrx_flat)
    flatten_emission_mtrx.append(emission_data)


In [391]:
emission_mtrx['pos0_cell3']

{1: [[2.898403920993961e-13,
   1.0283136935057907e-26,
   2.7608711258276563e-19,
   7.844834049135391e-20],
  [4.5359074374609086e-10,
   9.103226395969624e-13,
   2.0520511142006627e-67,
   2.716203778963272e-19],
  [1.0504111422719248e-11,
   2.712338826374149e-46,
   3.0207367790672962e-43,
   6.141698882323247e-69],
  [2.236619460915008e-11,
   7.5395596264151e-20,
   3.106575404463873e-92,
   3.3082301355541576e-47],
  [1.5675867025451018e-14,
   2.0027965243772648e-35,
   3.7463687713692244e-148,
   9.784831275494805e-14],
  [3.6956756903253385e-17,
   2.0031769654578662e-53,
   5.85344185576517e-32,
   1.4005484543401652e-35]],
 2: [[5.7899037744413684e-24,
   3.174579397956286e-17,
   1.9287299200806981e-13,
   1.1614055566731256e-103],
  [2.405994788194221e-11,
   3.12754444747096e-17,
   9.108143313514374e-15,
   3.633714996450186e-19],
  [5.878796116476981e-10,
   2.050256869776696e-64,
   1.347883646151249e-10,
   2.430060633482435e-21],
  [1.2644542321815142e-07,
   3.52

In [392]:
flatten_emission_mtrx[1]

['pos0_cell3',
 '[2.898403920993961e-13, 1.0283136935057907e-26, 2.7608711258276563e-19, 7.844834049135391e-20]',
 '[4.5359074374609086e-10, 9.103226395969624e-13, 2.0520511142006627e-67, 2.716203778963272e-19]',
 '[1.0504111422719248e-11, 2.712338826374149e-46, 3.0207367790672962e-43, 6.141698882323247e-69]',
 '[2.236619460915008e-11, 7.5395596264151e-20, 3.106575404463873e-92, 3.3082301355541576e-47]',
 '[1.5675867025451018e-14, 2.0027965243772648e-35, 3.7463687713692244e-148, 9.784831275494805e-14]',
 '[3.6956756903253385e-17, 2.0031769654578662e-53, 5.85344185576517e-32, 1.4005484543401652e-35]',
 '[5.7899037744413684e-24, 3.174579397956286e-17, 1.9287299200806981e-13, 1.1614055566731256e-103]',
 '[2.405994788194221e-11, 3.12754444747096e-17, 9.108143313514374e-15, 3.633714996450186e-19]',
 '[5.878796116476981e-10, 2.050256869776696e-64, 1.347883646151249e-10, 2.430060633482435e-21]',
 '[1.2644542321815142e-07, 3.5292546412941523e-75, 2.192578695551157e-17, 4.3511283084000015e-14]'

In [360]:
import csv

with open('/Users/gc3045/laml2_experiments/proc_realdata/baseMemoir.msa.txt', 'w') as f:
    writer = csv.writer(f)
    writer.writerows(flatten_char_mtrx)

In [393]:
import csv

with open('/Users/gc3045/laml2_experiments/proc_realdata/baseMemoir.emissions.txt', 'w') as f:
    writer = csv.writer(f)
    writer.writerows(flatten_emission_mtrx)

In [410]:
import ast
tmp_df = pd.read_csv('/Users/gc3045/laml2_experiments/proc_realdata/baseMemoir.emissions.small.txt')
emission_dict = dict()
for _, row in tmp_df.iterrows():
    print(row)
    cell_name = row.iloc[0]
    emission_dict[cell_name] = [] # list of dictionaries per site
    
    # Extract all columns after the first one
    other_columns = row.iloc[1:].to_dict()
    
    for column, value in other_columns.items():
        parsed_value = ast.literal_eval(value)
        emission_dict[cell_name].append(parsed_value)
    break

cell_names                                           pos0_cell3
c0_s0         [2.898403920993961e-13, 1.0283136935057907e-26...
c0_s1         [4.5359074374609086e-10, 9.103226395969624e-13...
c0_s2         [1.0504111422719248e-11, 2.712338826374149e-46...
c0_s3         [2.236619460915008e-11, 7.5395596264151e-20, 3...
c0_s4         [1.5675867025451018e-14, 2.0027965243772648e-3...
c0_s5         [3.6956756903253385e-17, 2.0031769654578662e-5...
c1_s0         [5.7899037744413684e-24, 3.174579397956286e-17...
c1_s1         [2.405994788194221e-11, 3.12754444747096e-17, ...
c1_s2         [5.878796116476981e-10, 2.050256869776696e-64,...
c1_s3         [1.2644542321815142e-07, 3.5292546412941523e-7...
c1_s4         [9.842629744836164e-09, 7.799523010425821e-26,...
c1_s5         [9.856235720136044e-13, 2.611086433519569e-20,...
Name: 0, dtype: object


In [411]:
emission_dict

{'pos0_cell3': [[2.898403920993961e-13,
   1.0283136935057907e-26,
   2.7608711258276563e-19,
   7.844834049135391e-20],
  [4.5359074374609086e-10,
   9.103226395969624e-13,
   2.0520511142006627e-67,
   2.716203778963272e-19],
  [1.0504111422719248e-11,
   2.712338826374149e-46,
   3.0207367790672962e-43,
   6.141698882323247e-69],
  [2.236619460915008e-11,
   7.5395596264151e-20,
   3.106575404463873e-92,
   3.3082301355541576e-47],
  [1.5675867025451018e-14,
   2.0027965243772648e-35,
   3.7463687713692244e-148,
   9.784831275494805e-14],
  [3.6956756903253385e-17,
   2.0031769654578662e-53,
   5.85344185576517e-32,
   1.4005484543401652e-35],
  [5.7899037744413684e-24,
   3.174579397956286e-17,
   1.9287299200806981e-13,
   1.1614055566731256e-103],
  [2.405994788194221e-11,
   3.12754444747096e-17,
   9.108143313514374e-15,
   3.633714996450186e-19],
  [5.878796116476981e-10,
   2.050256869776696e-64,
   1.347883646151249e-10,
   2.430060633482435e-21],
  [1.2644542321815142e-07,


In [361]:
file_path = '/Users/gc3045/laml2_experiments/proc_realdata/baseMemoir.msa.txt'
df = pd.read_csv(file_path)  # Assuming tab-separated values, change if necessary
matrix = df.iloc[:, 1:].values

value_counts = Counter(matrix.ravel())
print("\nValue counts:")
for value, count in value_counts.items():
    print(f"{value}: {count}")


Value counts:
0: 56373
3: 9790
2: 8607
-1: 62784
1: 15698


In [362]:
df

cell_names  c0_s0  c0_s1  c0_s2  c0_s3  c0_s4  c0_s5  c1_s0  c1_s1   
0      pos0_cell3      0      0      0      0      3      0      2      0  \
1      pos0_cell4      0      3      0      3      2      3     -1     -1   
2      pos0_cell5      0      2      0      2      2      1     -1     -1   
3      pos0_cell6      0      0      0      0      0      0     -1     -1   
4      pos0_cell7      3      1      1      1      3      1      1      1   
..            ...    ...    ...    ...    ...    ...    ...    ...    ...   
382  pos10_cell36     -1     -1     -1     -1     -1     -1     -1     -1   
383  pos10_cell37      1      3      2      2      1      1      0      0   
384  pos10_cell38      0      3      0      1      3      0     -1     -1   
385  pos10_cell39      0      3      0      2      3      3     -1     -1   
386  pos10_cell40      1      1      3      3      3      1     -1     -1   

     c1_s2  ...  c64_s2  c64_s3  c64_s4  c64_s5  c65_s0  c65_s1  c65_s2   
0        0  ...      -1      -1      -1      -1      -1      -1      -1  \
1       -1  ...      -1      -1      -1      -1      -1      -1      -1   
2       -1  ...      -1      -1      -1      -1       2       0       0   
3       -1  ...      -1      -1      -1      -1       0       0       2   
4        0  ...      -1      -1      -1      -1      -1      -1      -1   
..     ...  ...     ...     ...     ...     ...     ...     ...     ...   
382     -1  ...       0       3       3       0      -1      -1      -1   
383      0  ...      -1      -1      -1      -1       0       0       0   
384     -1  ...       2       0       0       0      -1      -1      -1   
385     -1  ...       0       3       0       0      -1      -1      -1   
386     -1  ...       2       0       0       0       0       0       0   

     c65_s3  c65_s4  c65_s5  
0        -1      -1      -1  
1        -1      -1      -1  
2         3       0       0  
3         0       0       1  
4        -1      -1      -1  
..      ...     ...     ...  
382      -1      -1      -1  
383       0       0       0  
384      -1      -1      -1  
385      -1      -1      -1  
386       3       0       0  

[387 rows x 397 columns]

In [351]:
value_counts[-1] / sum([value_counts[key] for key in value_counts])

0.40967817712003757

In [358]:
with open('/Users/gc3045/laml2_experiments/proc_realdata/baseMemoir.msa.small.txt', 'w') as f:
    writer = csv.writer(f)
    writer.writerows([x[:13] for x in flatten_char_mtrx[:6]])

In [394]:
with open('/Users/gc3045/laml2_experiments/proc_realdata/baseMemoir.emissions.small.txt', 'w') as f:
    writer = csv.writer(f)
    writer.writerows([x[:13] for x in flatten_emission_mtrx[:6]])

### check if we can drop some entries

Some positions (0/1, 7/8, 9/10) are offest images of the same colony. I will merge cells imaged twice, keeping the higher confidence one. The file reporting the correspondences is here: `/Users/gc3045/laml2_experiments/BaseMEM_Magic/Magic/Figures3_5_and_SupFigures2_4-6/lineage_analysis/multi-im_correspondence.txt`

If one has a cassette the other does not report, I will keep the extra information. 

In [191]:
matching = pd.read_csv("/Users/gc3045/laml2_experiments/BaseMEM_Magic/Magic/Figures3_5_and_SupFigures2_4-6/lineage_analysis/multi-im_correspondance.txt", sep='\t')
matching

Colony  Cell1  Cell2  Cell1_pos  Cell2_pos
0      p01      1      3          0          1
1      p01      2      4          0          1
2      p01      3      5          0          1
3      p01      4      6          0          1
4      p01      5      7          0          1
..     ...    ...    ...        ...        ...
101   p910     35     41          9         10
102   p910     36     42          9         10
103   p910     37     43          9         10
104   p910     38     44          9         10
105   p910     40     45          9         10

[106 rows x 5 columns]

In [192]:
# for each row in matching, extract the data from result_json

for index, row in matching.iterrows():
    # Construct string for Cell1 and Cell1_pos
    cell1_string = f"pos{row['Cell1_pos']}_cell{row['Cell1']}"
    cell2_string = f"pos{row['Cell2_pos']}_cell{row['Cell2']}"

    # print("cell1_string", cell1_string)
    for i, x in enumerate(result_json['cell_data']):
        # print(x['cell_name'])
        if x['cell_name'] == cell1_string or x['cell_name'] == cell2_string:
            # print(index, i, x['cell_name'] == cell1_string, x['cell_name'] == cell2_string)
            assert sum([x['cell_name'] == cell1_string, x['cell_name'] == cell2_string]) == 1
     

Actually, it's already been edited. result_json has gotten rid of any redundancies in being imaged twice. I may want to change the label of the position, but I think it's fine for now. 

### read code in

In [305]:
with open("/Users/gc3045/scmail_v1/LAML/examples/example5/baseMemoir_test_small.json", "r") as f:
    data = json.load(f)

In [306]:
K = len([x['cassette_id'] for x in data['cell_data'][0]['cassettes']])
J = len([key for key in data['cell_data'][0]['cassettes'][0]['count_data'][0].keys() if key.startswith('site_')])

In [307]:
K, J

(2, 6)

In [309]:
# data_struct: a mapping: cell_name -> (cassette -> cassette_state)
charMtrx_data_struct = {}
alphabet_dict = dict()
emission_dict = dict() # ****

K = len([x['cassette_id'] for x in data['cell_data'][0]['cassettes']])
J = len([key for key in data['cell_data'][0]['cassettes'][0]['count_data'][0].keys() if key.startswith('site_')])
print("K:", K, "J:", J)


for cell_data in data['cell_data']:
    cell_name = cell_data['cell_name']
    # save into data_struct
    charMtrx_data_struct[cell_name] = np.zeros(K, dtype=list)
    emission_dict[cell_name] = dict() # ****
    
    for cassette_data in cell_data['cassettes']:
        cassette_id = int(cassette_data['cassette_id']) - 1
        emission_dict[cell_name][cassette_id] = dict() # **** maps from obs -> true state
        
        # assert(len(cassette_data['count_data']) <= 1)
        if len(cassette_data['count_data']) == 1: 
            cassette_state = cassette_data['count_data'][0]['allele']
            charMtrx_data_struct[cell_name][cassette_id] = cassette_state
            
            
            # each cassette, each site has an alphabet
            if cassette_id not in alphabet_dict:
                alphabet_dict[cassette_id] = dict()
            for key in cassette_data['count_data'][0].keys():
                if key.startswith('site_'):
                    state = cassette_data['count_data'][0][key]
                    if key not in alphabet_dict[cassette_id]:
                        alphabet_dict[cassette_id][key] = {0, missing_char}
                    alphabet_dict[cassette_id][key].add(state)
                    
                    # each site in allele
                    site_idx = int(key[5:])
                    cassette_emission_dict = cassette_data['count_data'][0]['emissions_' + key]
                    emission_dict[cell_name][cassette_id][site_idx] = dict()
                    obs_state = state
                    for k, v in cassette_emission_dict.items():
                        true_state = int(key.split('_')[-1]) # probGen_KDE_true_state_0
                        emission_dict[cell_name][cassette_id][site_idx][obs_state] = dict()
                        emission_dict[cell_name][cassette_id][site_idx][obs_state][true_state] = v
                
        elif len(cassette_data['count_data']) == 0:
            charMtrx_data_struct[cell_name][cassette_id] = []

alphabet_data_struct = []
for cassette_index in alphabet_dict:
    new_cassette_list = []
    for site_index in range(J):
        new_target_site_list = list(alphabet_dict[cassette_index][f'site_{site_index}'])
        new_cassette_list.append(new_target_site_list)
    alphabet_data_struct.append(new_cassette_list)
          


K: 2 J: 6


In [310]:
alphabet = Alphabet(K,J,alphabet_data_struct)

In [311]:
DLT_data = CharMtrx(charMtrx_data_struct,alphabet)

In [315]:
DLT_data.alphabet.get_cassette_alphabet(0)

[(0, 0, 0, 0, 0, 0),
 (0, 0, 0, 0, 0, 1),
 (0, 0, 0, 0, 0, 3),
 (0, 0, 0, 0, 0, -1),
 (0, 0, 0, 0, 2, 0),
 (0, 0, 0, 0, 2, 1),
 (0, 0, 0, 0, 2, 3),
 (0, 0, 0, 0, 2, -1),
 (0, 0, 0, 0, 3, 0),
 (0, 0, 0, 0, 3, 1),
 (0, 0, 0, 0, 3, 3),
 (0, 0, 0, 0, 3, -1),
 (0, 0, 0, 0, -1, 0),
 (0, 0, 0, 0, -1, 1),
 (0, 0, 0, 0, -1, 3),
 (0, 0, 0, 0, -1, -1),
 (0, 0, 0, 1, 0, 0),
 (0, 0, 0, 1, 0, 1),
 (0, 0, 0, 1, 0, 3),
 (0, 0, 0, 1, 0, -1),
 (0, 0, 0, 1, 2, 0),
 (0, 0, 0, 1, 2, 1),
 (0, 0, 0, 1, 2, 3),
 (0, 0, 0, 1, 2, -1),
 (0, 0, 0, 1, 3, 0),
 (0, 0, 0, 1, 3, 1),
 (0, 0, 0, 1, 3, 3),
 (0, 0, 0, 1, 3, -1),
 (0, 0, 0, 1, -1, 0),
 (0, 0, 0, 1, -1, 1),
 (0, 0, 0, 1, -1, 3),
 (0, 0, 0, 1, -1, -1),
 (0, 0, 0, 2, 0, 0),
 (0, 0, 0, 2, 0, 1),
 (0, 0, 0, 2, 0, 3),
 (0, 0, 0, 2, 0, -1),
 (0, 0, 0, 2, 2, 0),
 (0, 0, 0, 2, 2, 1),
 (0, 0, 0, 2, 2, 3),
 (0, 0, 0, 2, 2, -1),
 (0, 0, 0, 2, 3, 0),
 (0, 0, 0, 2, 3, 1),
 (0, 0, 0, 2, 3, 3),
 (0, 0, 0, 2, 3, -1),
 (0, 0, 0, 2, -1, 0),
 (0, 0, 0, 2, -1, 1),
 (0, 0, 0, 2,

### write code for reading this in

In [205]:
with open("/Users/gc3045/laml2_experiments/proc_realdata/baseMemoir.json", "r") as f:
    data = json.load(f)
    

In [194]:
missing_char = -1

In [195]:
os.chdir('/Users/gc3045/scmail_v1/LAML/')
from laml_libs.Count_model.CharMtrx import CharMtrx
from laml_libs.Count_model.Alphabet import Alphabet

In [210]:
# data_struct: a mapping: cell_name -> (cassette -> cassette_state)
charMtrx_data_struct = {}
alphabet_dict = dict()
emission_dict = dict() # ****

K = len([x['cassette_id'] for x in data['cell_data'][0]['cassettes']])
J = len([key for key in data['cell_data'][0]['cassettes'][0]['count_data'][0].keys() if key.startswith('site_')])
print("K:", K, "J:", J)


K: 66 J: 6


In [220]:
for cell_data in data['cell_data']:
    cell_name = cell_data['cell_name']
    # save into data_struct
    charMtrx_data_struct[cell_name] = np.zeros(K, dtype=list)
    emission_dict[cell_name] = dict() # ****
    
    for cassette_data in cell_data['cassettes']:
        cassette_id = int(cassette_data['cassette_id']) - 1
        emission_dict[cell_name][cassette_id] = dict() # **** maps from obs -> true state
        
        # assert(len(cassette_data['count_data']) <= 1)
        if len(cassette_data['count_data']) == 1: 
            cassette_state = cassette_data['count_data'][0]['allele']
            charMtrx_data_struct[cell_name][cassette_id] = cassette_state
            
            
            # each cassette, each site has an alphabet
            if cassette_id not in alphabet_dict:
                alphabet_dict[cassette_id] = dict()
            for key in cassette_data['count_data'][0].keys():
                if key.startswith('site_'):
                    state = cassette_data['count_data'][0][key]
                    if key not in alphabet_dict[cassette_id]:
                        alphabet_dict[cassette_id][key] = {0, missing_char}
                    alphabet_dict[cassette_id][key].add(state)
                    
                    # each site in allele
                    site_idx = int(key[5:])
                    cassette_emission_dict = cassette_data['count_data'][0]['emissions_' + key]
                    emission_dict[cell_name][cassette_id][site_idx] = dict()
                    obs_state = state
                    for k, v in cassette_emission_dict.items():
                        true_state = int(key.split('_')[-1]) # probGen_KDE_true_state_0
                        emission_dict[cell_name][cassette_id][site_idx][obs_state] = dict()
                        emission_dict[cell_name][cassette_id][site_idx][obs_state][true_state] = v
                
        elif len(cassette_data['count_data']) == 0:
            charMtrx_data_struct[cell_name][cassette_id] = []

alphabet_data_struct = []
for cassette_index in alphabet_dict:
    new_cassette_list = []
    for site_index in range(J):
        new_target_site_list = list(alphabet_dict[cassette_index][f'site_{site_index}'])
        new_cassette_list.append(new_target_site_list)
    alphabet_data_struct.append(new_cassette_list)
          


In [221]:
len(charMtrx_data_struct['pos0_cell3']), len(charMtrx_data_struct['pos0_cell3'][0])

(66, 6)

In [222]:
charMtrx_data_struct['pos0_cell3']

array([list([0, 0, 0, 0, 3, 0]), list([2, 0, 0, 0, 0, 0]), list([]),
       list([]), list([]), list([1, 0, 0, 0, 0, 2]),
       list([1, 0, 1, 2, 1, 1]), list([]), list([1, 0, 0, 3, 0, 0]),
       list([]), list([]), list([]), list([1, 0, 0, 0, 1, 0]), list([]),
       list([1, 2, 2, 3, 1, 0]), list([2, 1, 2, 3, 1, 1]),
       list([0, 3, 0, 2, 3, 0]), list([]), list([]), list([]),
       list([1, 0, 0, 2, 0, 0]), list([]), list([]),
       list([0, 1, 0, 0, 0, 3]), list([0, 0, 0, 0, 2, 0]), list([]),
       list([]), list([]), list([0, 2, 0, 0, 0, 1]),
       list([1, 2, 1, 3, 3, 1]), list([]), list([]),
       list([3, 0, 0, 0, 0, 0]), list([]), list([]), list([]),
       list([0, 0, 0, 3, 0, 2]), list([]), list([]),
       list([2, 2, 0, 0, 2, 0]), list([]), list([2, 0, 0, 0, 0, 0]),
       list([]), list([1, 2, 0, 3, 3, 0]), list([]),
       list([0, 3, 0, 1, 1, 0]), list([]), list([1, 0, 0, 0, 1, 0]),
       list([2, 0, 0, 0, 1, 0]), list([0, 3, 3, 3, 0, 0]), list([]),
       lis

In [223]:
alphabet_dict

{0: {'site_0': {-1, 0, 1, 2, 3},
  'site_1': {-1, 0, 1, 2, 3},
  'site_2': {-1, 0, 1, 2, 3},
  'site_3': {-1, 0, 1, 2, 3},
  'site_4': {-1, 0, 1, 2, 3},
  'site_5': {-1, 0, 1, 2, 3}},
 1: {'site_0': {-1, 0, 1, 2, 3},
  'site_1': {-1, 0, 1, 2, 3},
  'site_2': {-1, 0, 1, 2, 3},
  'site_3': {-1, 0, 1, 2, 3},
  'site_4': {-1, 0, 1, 2, 3},
  'site_5': {-1, 0, 1, 2, 3}},
 5: {'site_0': {-1, 0, 1, 2, 3},
  'site_1': {-1, 0, 1, 2, 3},
  'site_2': {-1, 0, 1, 2, 3},
  'site_3': {-1, 0, 1, 2, 3},
  'site_4': {-1, 0, 1, 2, 3},
  'site_5': {-1, 0, 1, 2, 3}},
 6: {'site_0': {-1, 0, 1, 2, 3},
  'site_1': {-1, 0, 1, 2, 3},
  'site_2': {-1, 0, 1, 2, 3},
  'site_3': {-1, 0, 1, 2, 3},
  'site_4': {-1, 0, 1, 2, 3},
  'site_5': {-1, 0, 1, 2, 3}},
 8: {'site_0': {-1, 0, 1, 2, 3},
  'site_1': {-1, 0, 1, 2, 3},
  'site_2': {-1, 0, 1, 2, 3},
  'site_3': {-1, 0, 1, 2, 3},
  'site_4': {-1, 0, 1, 2, 3},
  'site_5': {-1, 0, 1, 2, 3}},
 12: {'site_0': {-1, 0, 1, 2, 3},
  'site_1': {-1, 0, 1, 2, 3},
  'site_2': {-1,

In [224]:
alphabet_data_struct

[[[0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1]],
 [[0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1]],
 [[0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1]],
 [[0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1]],
 [[0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1]],
 [[0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1]],
 [[0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1]],
 [[0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1],
  [0, 1, 2, 3, -1]],
 [[0, 1, 2, 3, -1],
  [0, 1, 2, 

In [225]:
alphabet = Alphabet(K,J,alphabet_data_struct)

In [226]:
DLT_data = CharMtrx(charMtrx_data_struct,alphabet)

In [227]:
DLT_data

In [228]:
emission_dict

{'pos0_cell3': {0: {0: {0: {0: 7.844834049135391e-20}},
   1: {0: {1: 2.716203778963272e-19}},
   2: {0: {2: 6.141698882323247e-69}},
   3: {0: {3: 3.3082301355541576e-47}},
   4: {3: {4: 9.784831275494805e-14}},
   5: {0: {5: 1.4005484543401652e-35}}},
  1: {0: {2: {0: 1.1614055566731256e-103}},
   1: {0: {1: 3.633714996450186e-19}},
   2: {0: {2: 2.430060633482435e-21}},
   3: {0: {3: 4.3511283084000015e-14}},
   4: {0: {4: 2.5174867444437613e-14}},
   5: {0: {5: 2.904449932454575e-19}}},
  5: {0: {1: {0: 7.885659433224286e-57}},
   1: {0: {1: 2.1571493706391762e-57}},
   2: {0: {2: 1.9508428066724844e-15}},
   3: {0: {3: 2.927556308192829e-18}},
   4: {0: {4: 7.204936263635148e-18}},
   5: {2: {5: 6.802100951161592e-72}}},
  6: {0: {1: {0: 1.4820455446100752e-19}},
   1: {0: {1: 4.576579171620877e-19}},
   2: {1: {2: 2.0714870199710623e-39}},
   3: {2: {3: 4.194758833683525e-36}},
   4: {1: {4: 7.584483057870403e-19}},
   5: {1: {5: 2.9600339659016346e-51}}},
  8: {0: {1: {0: 1.0491

In [431]:
for i, colony in df.groupby('position_number'):
    print("position", i)
    lowest_mean = 1
    lowest_cell = ''
    for j, cell in colony.groupby('cell_number'):
#         if i == 2.0 and j == 22.0:
#             continue
#         if i == 6.0 and j == 15.0:
#             continue
        cell_mean = cell['maxpostprobstate_at_site'].mean()
        if cell_mean < lowest_mean:
            lowest_mean = cell_mean
            lowest_cell = j
    print("cell", lowest_cell, lowest_mean)

position 0.0
cell 26.0 0.4166666666666667
position 1.0
cell 23.0 0.0
position 2.0
cell 22.0 0.32945736434108525
position 3.0
cell 11.0 0.5064102564102564
position 4.0
cell 20.0 0.48148148148148145
position 5.0
cell 3.0 0.5352564102564102
position 6.0
cell 15.0 0.3923611111111111
position 7.0
cell 38.0 0.3108108108108108
position 8.0
cell 36.0 0.3143939393939394
position 9.0
cell 25.0 0.4864864864864865
position 10.0
cell 29.0 0.45121951219512196


In [432]:
for i, colony in df.groupby('position_number'):
    print("position", i)
    
    all_cells = []
    for j, cell in colony.groupby('cell_number'):
        cell_mean = cell['maxpostprobstate_at_site'].mean()
        all_cells.append(cell_mean)
    print("avg. maxpostprobstate over all cells", np.mean(all_cells))
    
    # make this a boxplot

position 0.0
avg. maxpostprobstate over all cells 0.6029247918190896
position 1.0
avg. maxpostprobstate over all cells 0.5487766994101144
position 2.0
avg. maxpostprobstate over all cells 0.5279816825385266
position 3.0
avg. maxpostprobstate over all cells 0.5877032712742091
position 4.0
avg. maxpostprobstate over all cells 0.6392817297250523
position 5.0
avg. maxpostprobstate over all cells 0.6611579015781764
position 6.0
avg. maxpostprobstate over all cells 0.4833773086028097
position 7.0
avg. maxpostprobstate over all cells 0.65143579312256
position 8.0
avg. maxpostprobstate over all cells 0.528529639005601
position 9.0
avg. maxpostprobstate over all cells 0.6529187421256655
position 10.0
avg. maxpostprobstate over all cells 0.6546962080671077


In [433]:
df

integration_barcode  cell_number  dot_number  position_number   
0                      1.0          1.0        57.0              1.0  \
1                      1.0          1.0        57.0              1.0   
2                      1.0          1.0        57.0              1.0   
3                      1.0          1.0        57.0              1.0   
4                      1.0          1.0        57.0              1.0   
...                    ...          ...         ...              ...   
90463                  9.0          9.0       649.0              9.0   
90464                  9.0          9.0       649.0              9.0   
90465                  9.0          9.0       649.0              9.0   
90466                  9.0          9.0       649.0              9.0   
90467                  9.0          9.0       649.0              9.0   

       site_index  feature_1  feature_2  feature_3  feature_4  feature_5  ...   
0             1.0  10.984123   8.966101  10.065734   7.761319   6.930495  ...  \
1             2.0  10.861515   8.056427   8.837100  11.704025   6.620073  ...   
2             3.0   7.203406  10.781100   7.641564   8.145260   2.833213  ...   
3             4.0   6.924612  10.706117   7.285507   7.573017   2.484907  ...   
4             5.0  10.343901   8.582606  10.566330  10.339126   6.424869  ...   
...           ...        ...        ...        ...        ...        ...  ...   
90463         2.0   6.735780  10.173782   7.367709   8.249836   3.091042  ...   
90464         3.0   6.753438  10.685995   7.773174   7.355002   2.639057  ...   
90465         4.0   5.176150  10.653606   8.835792   5.726848   0.000000  ...   
90466         5.0  10.038106   8.198089   5.505332  10.433056   6.224558  ...   
90467         6.0   8.503297  10.389118   7.581210   8.083020   4.727388  ...   

       intensity_channel2  intensity_channel3  intensity_channel4   
0                    65.0                35.0                65.0  \
1                    65.0                65.0                50.0   
2                    41.0                 5.0                65.0   
3                    41.0                 4.0                65.0   
4                    65.0                42.0                39.0   
...                   ...                 ...                 ...   
90463                27.0                35.0                35.0   
90464                35.0                35.0                35.0   
90465                35.0                35.0                35.0   
90466                35.0                35.0                35.0   
90467                35.0                35.0                35.0   

       maxpostprobstate_at_site  maxpostprobval_at_site       state_0   
0                           1.0                0.909489  5.995518e-18  \
1                           3.0                0.644814  1.999991e-17   
2                           0.0                0.940735  1.881959e-11   
3                           0.0                0.942045  1.603485e-14   
4                           1.0                0.567286  1.890085e-35   
...                         ...                     ...           ...   
90463                       0.0                0.979866  1.193092e-09   
90464                       0.0                0.987961  1.290770e-07   
90465                       0.0                0.966041  3.868813e-09   
90466                       1.0                0.664211  1.636422e-23   
90467                       0.0                0.913224  9.545623e-14   

            state_1        state_2       state_3  KDE_max_state  
0      1.132963e-10   6.091644e-19  1.705798e-69              1  
1      1.399712e-13   1.332736e-19  4.175912e-14              1  
2      6.889248e-19   4.426716e-16  6.129712e-13              0  
3      7.138131e-29   5.265846e-16  1.032066e-32              0  
4      2.280929e-14   1.780643e-15  9.252995e-19              1  
...             ...            ...           ...            ...  
9